# **Operações na Média vs Aleatório**

## ***1. Explicação***

Objetivo desse estudo é analisar uma tendência de alta e identificar se candles seguintes ao candle que toca na média móvel (20) tem maior probabilidade de ser positivo em relação aos demais candles acima da média mas que não tocam nela.

**Premissas para uma tendência:**

- Ter pelo menos 3 candles completamente acima da média móvel de 20;
- A média móvel de 20 períodos estar acima da média móvel de 60 períodos (20 do 15m);
- A média móvel de 60 estar acima da média móvel de 200 períodos.

**Premissas para toque na média:**
- Candle anterior estar em tendência;
- Candle do toque ter mínima menor ou igual à média e close maior que a média.

## ***2. Instalando e Importando Bibliotecas***

In [1]:
!pip install yfinance
!pip install plotly

import pandas as pd
import yfinance as yf
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


## ***3. Importando Dados do ativo via yfinance***

In [2]:
ticker = 'AAPL'
dados = yf.download(ticker, period='max', interval='1d')

[*********************100%***********************]  1 of 1 completed


## ***4. Criar médias médias móveis necessárias para o estudo:***

In [3]:
sma_20 = 20
sma_50 = 50 
sma_200 = 200 
dados['Sma_20'] = dados['Close'].rolling(sma_20).mean()
dados['Sma_50'] = dados['Close'].rolling(sma_50).mean()
dados['Sma_200'] = dados['Close'].rolling(sma_200).mean()

In [ ]:
df_figure = dados
fig = make_subplots(rows=1, cols=1)

fig.add_trace(go.Candlestick(name=ticker, x=df_figure.index, open=df_figure['Open'], high = df_figure['High'], 
                             low=df_figure['Low'], close=df_figure['Close']), row=1,col=1)

fig.add_trace(go.Scatter(name='Sma_20', x=df_figure.index, y=df_figure['Sma_20'], marker_color='blue'), row=1, col=1)
fig.add_trace(go.Scatter(name='Sma_50', x=df_figure.index, y=df_figure['Sma_50'], marker_color='red'), row=1, col=1)
fig.add_trace(go.Scatter(name='Sma_200', x=df_figure.index, y=df_figure['Sma_200'], marker_color='black'), row=1, col=1)


#fig.update_xaxes(title_text="<b> Data",rangebreaks=[dict(bounds=["sat", "mon"])])
fig.update_layout(xaxis_rangeslider_visible=False, title_text='<b>Candlesticks', 
                  yaxis1_title="<b> Preço",
                  font=dict(family="Arial", size=15, color="black"), margin=dict(l=50, r=20, t=70, b=20),
                  template = 'simple_white', paper_bgcolor="#f7f8fa",
                  width=1200, height=500)
fig.show()

## ***Criar condições para tendência com def:***

In [5]:
dados['Low_Shift_1'] = dados['Low'].shift(1)
dados['Low_Shift_2'] = dados['Low'].shift(2)
dados['Sma_20_Shift_1'] = dados['Sma_20'].shift(1)
dados['Sma_20_Shift_2'] = dados['Sma_20'].shift(2)

In [6]:
def cond_tendencia(df):
    if df['Low_Shift_2'] > df['Sma_20_Shift_2'] and df['Low_Shift_1'] > df['Sma_20_Shift_1'] and df['Low'] > df['Sma_20'] and df['Sma_20'] > df['Sma_50'] and df['Sma_50'] > df['Sma_200']:
        return True
    else:
        return False   

dados['Tendencia'] = dados.apply(cond_tendencia, axis=1)
dados.tail()

Open        High         Low       Close   Adj Close  \
Date                                                                     
2023-02-15  153.110001  155.500000  152.880005  155.330002  155.330002   
2023-02-16  153.509995  156.330002  153.350006  153.710007  153.710007   
2023-02-17  152.350006  153.000000  150.850006  152.550003  152.550003   
2023-02-21  150.199997  151.300003  148.410004  148.479996  148.479996   
2023-02-22  148.869995  149.949997  147.160004  148.910004  148.910004   

              Volume      Sma_20      Sma_50    Sma_200  Low_Shift_1  \
Date                                                                   
2023-02-15  65669300  147.456499  139.763599  147.44965   150.860001   
2023-02-16  68167900  148.378499  139.905199  147.42840   152.880005   
2023-02-17  59095900  149.112499  140.097999  147.39375   153.350006   
2023-02-21  58867200  149.480999  140.248799  147.30605   150.850006   
2023-02-22  50939700  149.799999  140.373999  147.26675   148.410004   

            Low_Shift_2  Sma_20_Shift_1  Sma_20_Shift_2  Tendencia  
Date                                                                
2023-02-15   150.919998      146.450499      145.587499      False  
2023-02-16   150.860001      147.456499      146.450499      False  
2023-02-17   152.880005      148.378499      147.456499      False  
2023-02-21   153.350006      149.112499      148.378499      False  
2023-02-22   150.850006      149.480999      149.112499      False

### ***Plotando***

In [ ]:
df_figure = dados
fig = make_subplots(rows=1, cols=1)

fig.add_trace(go.Candlestick(name=ticker, x=df_figure.index, open=df_figure['Open'], high = df_figure['High'], 
                             low=df_figure['Low'], close=df_figure['Close']), row=1,col=1)

fig.add_trace(go.Scatter(name='Sma_20', x=df_figure.index, y=df_figure['Sma_20'], marker_color='gray'), row=1, col=1)
fig.add_trace(go.Scatter(name='Sma_50', x=df_figure.index, y=df_figure['Sma_50'], marker_color='gray'), row=1, col=1)
fig.add_trace(go.Scatter(name='Sma_200', x=df_figure.index, y=df_figure['Sma_200'], marker_color='black'), row=1, col=1)
fig.add_trace(go.Scatter(name='Tendencia', x=df_figure.index, y=(1 - .005)*df_figure["Low"].where(df_figure["Tendencia"] == True), 
mode='markers', marker=dict(color='Blue', size=5)))


fig.update_xaxes(title_text="<b> Data",rangebreaks=[dict(bounds=["sat", "mon"])])
fig.update_layout(xaxis_rangeslider_visible=False, showlegend=False)
fig.update_layout(xaxis_rangeslider_visible=False, title_text='<b>Candlesticks', 
                  yaxis1_title="<b> Preço",
                  font=dict(family="Arial", size=15, color="black"), margin=dict(l=50, r=20, t=70, b=20),
                  template = 'simple_white', paper_bgcolor="#f7f8fa",
                  width=1200, height=500)
fig.show()

## ***Criar condições toque média***

In [8]:
dados['Toque'] = (dados['Tendencia'].shift(1)==True) & ((dados['Low']<=dados['Sma_20']) & (dados['Close']>dados['Sma_20']) )

In [ ]:
df_figure = dados
fig = make_subplots(rows=1, cols=1)

fig.add_trace(go.Candlestick(name=ticker, x=df_figure.index, open=df_figure['Open'], high = df_figure['High'], 
                             low=df_figure['Low'], close=df_figure['Close']), row=1,col=1)

fig.add_trace(go.Scatter(name='Sma_20', x=df_figure.index, y=df_figure['Sma_20'], marker_color='gray'), row=1, col=1)
fig.add_trace(go.Scatter(name='Sma_50', x=df_figure.index, y=df_figure['Sma_50'], marker_color='gray'), row=1, col=1)
fig.add_trace(go.Scatter(name='Sma_200', x=df_figure.index, y=df_figure['Sma_200'], marker_color='black'), row=1, col=1)
fig.add_trace(go.Scatter(name='tendencia', x=df_figure.index, y=(1 - .005)*df_figure["Low"].where(df_figure["Tendencia"] == True), 
mode='markers', marker=dict(color='Blue', size=5)))
fig.add_trace(go.Scatter(name='toque', x=df_figure.index, y=(1 + .005)*df_figure["Low"].where(df_figure["Toque"] == True), 
mode='markers', marker=dict(color='Red', size=5)))

#fig.update_xaxes(title_text="<b> Data",rangebreaks=[dict(bounds=["sat", "mon"])])
fig.update_layout(xaxis_rangeslider_visible=False, showlegend=False)
fig.update_layout(xaxis_rangeslider_visible=False, title_text='<b>Candlesticks', 
                  yaxis1_title="<b> Preço",
                  font=dict(family="Arial", size=15, color="black"), margin=dict(l=50, r=20, t=70, b=20),
                  template = 'simple_white', paper_bgcolor="#f7f8fa",
                  width=1200, height=500)
fig.show()

## ***Análise estatística***

In [10]:
dados['Candles_Seguintes_Ao_Que_Tocam'] = (dados['Toque'].shift(1) == True).astype(int)
dados['Candles_Seguintes_Ao_Que_Nao_Tocam'] = ((dados['Tendencia'].shift(1)==True) & ((dados['Toque'] == False))).astype(int)
dados['Candles_Seguintes_Ao_Que_Tocam_Positivos'] = ((dados['Candles_Seguintes_Ao_Que_Tocam'] == 1) & (dados['Close'] > dados['Open'])).astype(int)
dados['Candles_Seguintes_Ao_Que_Nao_Tocam_Positivos'] = ((dados['Candles_Seguintes_Ao_Que_Nao_Tocam'] == 1) & (dados['Close'] > dados['Open'])).astype(int)

### ***Resultados***

In [11]:
dados['Candles_Seguintes_Ao_Que_Tocam_Positivos'].sum() / dados['Candles_Seguintes_Ao_Que_Tocam'].sum()

0.46938775510204084

In [12]:
dados['Candles_Seguintes_Ao_Que_Nao_Tocam_Positivos'].sum() / dados['Candles_Seguintes_Ao_Que_Nao_Tocam'].sum()

0.5044083526682135

#### ***Plot test***

In [13]:
df_figure = dados
fig = make_subplots(rows=1, cols=1)

fig.add_trace(go.Candlestick(name=ticker, x=df_figure.index, open=df_figure['Open'], high = df_figure['High'], 
                             low=df_figure['Low'], close=df_figure['Close']), row=1,col=1)

fig.add_trace(go.Scatter(name='Sma_20', x=df_figure.index, y=df_figure['Sma_20'], marker_color='gray'), row=1, col=1)
fig.add_trace(go.Scatter(name='Sma_50', x=df_figure.index, y=df_figure['Sma_50'], marker_color='gray'), row=1, col=1)
fig.add_trace(go.Scatter(name='Sma_200', x=df_figure.index, y=df_figure['Sma_200'], marker_color='gray'), row=1, col=1)
fig.add_trace(go.Scatter(name='tendencia', x=df_figure.index, y=(1 - .005)*df_figure["Low"].where(df_figure["Tendencia"] == True), 
mode='markers', marker=dict(color='Blue', size=6)))
fig.add_trace(go.Scatter(name='toque', x=df_figure.index, y=(1 - .005)*df_figure["Low"].where(df_figure["Toque"] == True), 
mode='markers', marker=dict(color='Red', size=6)))
fig.add_trace(go.Scatter(name='Candles_Seguintes_Ao_Que_Tocam', x=df_figure.index, y=(1 + .005)*df_figure["High"].where(df_figure["Candles_Seguintes_Ao_Que_Tocam"] == True), 
mode='markers', marker=dict(color='Green', size=6)))
fig.add_trace(go.Scatter(name='Candles_Seguintes_Ao_Que_Tocam_Positivos', x=df_figure.index, y=(1 + .010)*df_figure["High"].where(df_figure["Candles_Seguintes_Ao_Que_Tocam_Positivos"] == True), 
mode='markers', marker=dict(color='Green', size=6)))
fig.add_trace(go.Scatter(name='Candles_Seguintes_Ao_Que_Nao_Tocam', x=df_figure.index, y=(1 + .005)*df_figure["High"].where(df_figure["Candles_Seguintes_Ao_Que_Nao_Tocam"] == True), 
mode='markers', marker=dict(color='Purple', size=6)))
fig.add_trace(go.Scatter(name='Candles_Seguintes_Ao_Que_Nao_Tocam_Positivos', x=df_figure.index, y=(1 + .010)*df_figure["High"].where(df_figure["Candles_Seguintes_Ao_Que_Nao_Tocam_Positivos"] == True), 
mode='markers', marker=dict(color='Purple', size=6)))


fig.update_xaxes(title_text="<b> Data",rangebreaks=[dict(bounds=["sat", "mon"])])
fig.update_layout(xaxis_rangeslider_visible=False, showlegend=False)
fig.update_layout(xaxis_rangeslider_visible=False, title_text='<b>Candlesticks', 
                  yaxis1_title="<b> Preço",
                  font=dict(family="Arial", size=15, color="black"), margin=dict(l=50, r=20, t=70, b=20),
                  template = 'simple_white', paper_bgcolor="#f7f8fa",
                  width=1200, height=500)
fig.show()